In [1]:
cd /home/yuchen/pulse2percept

/home/yuchen/pulse2percept


In [2]:
from pulse2percept.models import BiphasicAxonMapModel, AxonMapModel
from pulse2percept.model_selection import ParticleSwarmOptimizer
from pulse2percept.implants import ArgusII
import shapes
import pandas as pd
import pickle
import matplotlib.pyplot as plt
import numpy as np

In [3]:
s2 = shapes.subject_params['12-005']
implant, model = shapes.model_from_params(s2, biphasic=False)
model.xystep=0.25

estimator = shapes.AxonMapEstimator(implant=implant, model=model, mse_params=['area', "major_axis_length", "minor_axis_length"], loss_fn='r2', scale_features=False, resize=True)
search_params = {
    'rho': (10, 1000),
    'axlambda': (10, 2000)
}
opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=100, has_loss_function=True)

data = shapes.load_shapes("/home/yuchen/shapes/data/shapes.h5", subjects=['12-005'], stim_class='SingleElectrode')
x = data[['amp1', 'freq', 'pdur', 'electrode1']]
y = data['image']

y_moments = estimator.compute_moments(y)
averaged_moments = data
averaged_moments[['area', 'eccentricity', 'orientation']] = y_moments
averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation'].mean()
x = averaged_moments.index.to_frame().reset_index(drop=True)

train_mse = []
test_mse = []
train_size = []
test_size = []
estimator_params = []
filename_lst = []
electrode_lst=['A1','A4','A8','B1','B3','B9','C10','C7','D1','D10','D7']  # in case the server disconnects when program is running

for electrode in x.electrode1.unique():
    if electrode not in electrode_lst:
        estimator = shapes.AxonMapEstimator(implant=implant, model=model, mse_params=['area', "major_axis_length", "minor_axis_length"], loss_fn='r2', scale_features=False, resize=True)
        y_moments = estimator.compute_moments(y)
        averaged_moments = data
        averaged_moments[['area', 'eccentricity', 'orientation']] = y_moments
        averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation'].mean()
        # generate filename
        filename = 'Axon_' + 's2_' + electrode + '.pickle'
        filename_lst.append(filename)

        # get train_x and train_y
        train_x = x[x.electrode1 != electrode].reset_index(drop=True)
        train_y = averaged_moments.drop(electrode,level=2, axis=0)
        train_size.append(len(train_x))
        
        # fitting and finding the best parameter
        best_mse = 0
        best_score = 99999
        best_estimator = estimator
        for itr in range(3):
            print("Now we are fitting: " + filename[:-7] + " round " + str(itr))
            opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=100, has_loss_function=True)
            opt.fit(train_x, train_y)
            score = estimator.score(train_x, train_y,return_mses=True)
            if score[0]<best_score: 
                best_score = score[0]
                best_estimator = estimator
                best_mse = score[1]

        # store train results and estimator
        train_mse.append([best_score,best_mse])
        estimator = best_estimator
        pickle.dump(estimator, open(filename, 'wb'))
        estimator_params.append(estimator.get_params())
        
        # test (recompute y moments)
        estimator.mse_params = ['moments_central', "area", "eccentricity", "major_axis_length", "minor_axis_length", "orientation"]
        estimator.scale_features=True
        y_moments = pd.DataFrame(estimator.compute_moments(y, fit_scaler=True))
        result = pd.concat([y_moments, data[['amp1', 'freq', 'electrode1','pdur']]], axis=1, join='inner')
        test_y = result.groupby(['amp1', 'freq', 'electrode1','pdur']).mean().loc[pd.IndexSlice[:, :,electrode], :]
        test_x = x[x.electrode1 == electrode].reset_index(drop=True)

        # store test results
        test_size.append(len(test_x))
        test_mse.append(estimator.score(test_x, test_y, return_mses=True))
        
        rho = []
        axlambda = []
        train_MSE_combined = []
        train_MSE_area = []
        train_MSE_major_axis_length = []
        train_MSE_minor_axis_length = []

        test_MSE_combined = []
        test_MSE_M00 = []
        test_MSE_M02 = []
        test_MSE_M11 = []
        test_MSE_M12 = []
        test_MSE_M20 = []
        test_MSE_M21 = []
        test_MSE_M22 = []

        test_MSE_area = []
        test_MSE_eccentricity = []
        test_MSE_major_axis_length = []
        test_MSE_minor_axis_length = []
        test_MSE_orientation = []


        rho.append(estimator_params[-1]['rho'])
        axlambda.append(estimator_params[-1]['axlambda'])
        train_MSE_combined.append(train_mse[-1][0])
        train_MSE_area.append(train_mse[-1][1][0])
        train_MSE_major_axis_length.append(train_mse[-1][1][1])
        train_MSE_minor_axis_length.append(train_mse[-1][1][2])
        
        test_MSE_combined.append(test_mse[-1][0])
        test_MSE_M00.append(test_mse[-1][1][0])
        test_MSE_M02.append(test_mse[-1][1][1])
        test_MSE_M11.append(test_mse[-1][1][2])
        test_MSE_M12.append(test_mse[-1][1][3])
        test_MSE_M20.append(test_mse[-1][1][4])
        test_MSE_M21.append(test_mse[-1][1][5])
        test_MSE_M22.append(test_mse[-1][1][6])

        test_MSE_area.append(test_mse[-1][1][7])
        test_MSE_eccentricity.append(test_mse[-1][1][8])    
        test_MSE_major_axis_length.append(test_mse[-1][1][9])
        test_MSE_minor_axis_length.append(test_mse[-1][1][10])
        test_MSE_orientation.append(test_mse[-1][1][11])

        df = pd.DataFrame({'electrode':[electrode],
                       'rho':rho,
                       'axlambda':axlambda,
                       'train_combined':train_MSE_combined,
                       'train_area':train_MSE_area,
                       'train_MSE_major_axis_length':train_MSE_major_axis_length,
                       'train_MSE_minor_axis_length':train_MSE_minor_axis_length,

                       'test_combined':test_MSE_combined,
                       'test_M00':test_MSE_M00,
                       'test_M02':test_MSE_M02,
                       'test_M11':test_MSE_M11,
                       'test_M12':test_MSE_M12,
                       'test_M20':test_MSE_M20,
                       'test_M21':test_MSE_M21,
                       'test_M22':test_MSE_M22,
                       'test_area':test_MSE_area,
                       'test_eccentricity':test_MSE_eccentricity,
                       'test_major_axis_length':test_MSE_major_axis_length,
                       'test_minor_axis_length':test_MSE_minor_axis_length,
                       'test_orientation':test_MSE_orientation,


                        'train_size': [train_size[-1]],
                      'test_size':[test_size[-1]],
                      'filename':filename})
        df.to_csv("/home/yuchen/shapes/(new)estimator/" + filename[:-7] + '.csv', encoding='utf-8')

Now we are fitting: Axon_s2_D8 round 0
score:340.571, rho:568.6, lambda:578.0, empty:0, scores:['area:274.1', 'major_axis_length:3.8', 'minor_axis_length:62.7']
score:153.939, rho:378.6, lambda:1175.8, empty:0, scores:['area:127.1', 'major_axis_length:4.7', 'minor_axis_length:22.2']
score:197.985, rho:440.5, lambda:952.0, empty:0, scores:['area:161.2', 'major_axis_length:4.0', 'minor_axis_length:32.7']
score:73.291, rho:396.2, lambda:361.8, empty:0, scores:['area:49.0', 'major_axis_length:1.1', 'minor_axis_length:23.1']
score:38.015, rho:357.3, lambda:89.0, empty:0, scores:['area:20.4', 'major_axis_length:1.1', 'minor_axis_length:16.5']
score:1566.171, rho:745.7, lambda:1786.3, empty:0, scores:['area:1420.7', 'major_axis_length:20.3', 'minor_axis_length:125.2']
score:1434.851, rho:917.6, lambda:24.5, empty:0, scores:['area:1253.0', 'major_axis_length:11.3', 'minor_axis_length:170.6']
score:1586.511, rho:836.3, lambda:893.0, empty:0, scores:['area:1410.0', 'major_axis_length:14.1', 'min

In [ ]:
s3 = shapes.subject_params['51-009']
implant, model = shapes.model_from_params(s3, biphasic=False)
model.xystep=0.25

estimator = shapes.AxonMapEstimator(implant=implant, model=model, mse_params=['area', "major_axis_length", "minor_axis_length"], loss_fn='r2', scale_features=False, resize=True)
search_params = {
    'rho': (5, 1000),
    'axlambda': (10, 2000)
}
opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=100, has_loss_function=True)

data = shapes.load_shapes("/home/yuchen/shapes/data/shapes.h5", subjects=['51-009'], stim_class='SingleElectrode')
x = data[['amp1', 'freq', 'pdur', 'electrode1']]
y = data['image']

y_moments = estimator.compute_moments(y)
averaged_moments = data
averaged_moments[['area', 'eccentricity', 'orientation']] = y_moments
averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation'].mean()
x = averaged_moments.index.to_frame().reset_index(drop=True)

train_mse = []
test_mse = []
train_size = []
test_size = []
estimator_params = []
filename_lst = []
electrode_lst=['D8','E9','F4','A10','A2','A4','A6','A8','B3','B4','B9','C1','C10','C3','C5','C6']
for electrode in x.electrode1.unique():
    if electrode not in electrode_lst:
        estimator = shapes.AxonMapEstimator(implant=implant, model=model, mse_params=['area', "major_axis_length", "minor_axis_length"], loss_fn='r2', scale_features=False, resize=True)
        y_moments = estimator.compute_moments(y)
        averaged_moments = data
        averaged_moments[['area', 'eccentricity', 'orientation']] = y_moments
        averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation'].mean()
        # generate filename
        filename = 'Axon_' + 's3_' + electrode + '.pickle'
        filename_lst.append(filename)

        # get train_x and train_y
        train_x = x[x.electrode1 != electrode].reset_index(drop=True)
        train_y = averaged_moments.drop(electrode,level=2, axis=0)
        train_size.append(len(train_x))
        
        # fitting and finding the best parameter
        best_mse = 0
        best_score = 99999
        best_estimator = estimator
        for itr in range(3):
            print("Now we are fitting: " + filename[:-7] + " round " + str(itr))
            opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=100, has_loss_function=True)
            opt.fit(train_x, train_y)
            score = estimator.score(train_x, train_y,return_mses=True)
            if score[0]<best_score: 
                best_score = score[0]
                best_estimator = estimator
                best_mse = score[1]

        # store train results and estimator
        train_mse.append([best_score,best_mse])
        estimator = best_estimator
        pickle.dump(estimator, open(filename, 'wb'))
        estimator_params.append(estimator.get_params())
        
        # test (recompute y moments)
        estimator.mse_params = ['moments_central', "area", "eccentricity", "major_axis_length", "minor_axis_length", "orientation"]
        estimator.scale_features=True
        y_moments = pd.DataFrame(estimator.compute_moments(y, fit_scaler=True))
        result = pd.concat([y_moments, data[['amp1', 'freq', 'electrode1','pdur']]], axis=1, join='inner')
        test_y = result.groupby(['amp1', 'freq', 'electrode1','pdur']).mean().loc[pd.IndexSlice[:, :,electrode], :]
        test_x = x[x.electrode1 == electrode].reset_index(drop=True)

        # store test results
        test_size.append(len(test_x))
        test_mse.append(estimator.score(test_x, test_y, return_mses=True))
        
        rho = []
        axlambda = []
        train_MSE_combined = []
        train_MSE_area = []
        train_MSE_major_axis_length = []
        train_MSE_minor_axis_length = []

        test_MSE_combined = []
        test_MSE_M00 = []
        test_MSE_M02 = []
        test_MSE_M11 = []
        test_MSE_M12 = []
        test_MSE_M20 = []
        test_MSE_M21 = []
        test_MSE_M22 = []

        test_MSE_area = []
        test_MSE_eccentricity = []
        test_MSE_major_axis_length = []
        test_MSE_minor_axis_length = []
        test_MSE_orientation = []


        rho.append(estimator_params[-1]['rho'])
        axlambda.append(estimator_params[-1]['axlambda'])
        train_MSE_combined.append(train_mse[-1][0])
        train_MSE_area.append(train_mse[-1][1][0])
        train_MSE_major_axis_length.append(train_mse[-1][1][1])
        train_MSE_minor_axis_length.append(train_mse[-1][1][2])
        
        test_MSE_combined.append(test_mse[-1][0])
        test_MSE_M00.append(test_mse[-1][1][0])
        test_MSE_M02.append(test_mse[-1][1][1])
        test_MSE_M11.append(test_mse[-1][1][2])
        test_MSE_M12.append(test_mse[-1][1][3])
        test_MSE_M20.append(test_mse[-1][1][4])
        test_MSE_M21.append(test_mse[-1][1][5])
        test_MSE_M22.append(test_mse[-1][1][6])

        test_MSE_area.append(test_mse[-1][1][7])
        test_MSE_eccentricity.append(test_mse[-1][1][8])    
        test_MSE_major_axis_length.append(test_mse[-1][1][9])
        test_MSE_minor_axis_length.append(test_mse[-1][1][10])
        test_MSE_orientation.append(test_mse[-1][1][11])

        df = pd.DataFrame({'electrode':[electrode],
                       'rho':rho,
                       'axlambda':axlambda,
                       'train_combined':train_MSE_combined,
                       'train_area':train_MSE_area,
                       'train_MSE_major_axis_length':train_MSE_major_axis_length,
                       'train_MSE_minor_axis_length':train_MSE_minor_axis_length,

                       'test_combined':test_MSE_combined,
                       'test_M00':test_MSE_M00,
                       'test_M02':test_MSE_M02,
                       'test_M11':test_MSE_M11,
                       'test_M12':test_MSE_M12,
                       'test_M20':test_MSE_M20,
                       'test_M21':test_MSE_M21,
                       'test_M22':test_MSE_M22,
                       'test_area':test_MSE_area,
                       'test_eccentricity':test_MSE_eccentricity,
                       'test_major_axis_length':test_MSE_major_axis_length,
                       'test_minor_axis_length':test_MSE_minor_axis_length,
                       'test_orientation':test_MSE_orientation,


                        'train_size': [train_size[-1]],
                      'test_size':[test_size[-1]],
                      'filename':filename})
        df.to_csv("/home/yuchen/shapes/(new)estimator/" + filename[:-7] + '.csv', encoding='utf-8')

Now we are fitting: Axon_s3_C8 round 0
score:8854.465, rho:786.4, lambda:61.9, empty:0, scores:['area:7108.0', 'major_axis_length:3.0', 'minor_axis_length:1743.5']
score:103.143, rho:132.6, lambda:1116.7, empty:0, scores:['area:67.1', 'major_axis_length:0.8', 'minor_axis_length:35.3']
score:9855.935, rho:801.9, lambda:237.6, empty:0, scores:['area:8008.2', 'major_axis_length:3.2', 'minor_axis_length:1844.5']
score:1188.437, rho:291.5, lambda:1818.3, empty:0, scores:['area:943.6', 'major_axis_length:1.5', 'minor_axis_length:243.3']
score:9116.900, rho:654.7, lambda:1800.9, empty:0, scores:['area:7872.0', 'major_axis_length:4.9', 'minor_axis_length:1240.0']
score:2406.009, rho:498.3, lambda:677.2, empty:0, scores:['area:1725.3', 'major_axis_length:1.3', 'minor_axis_length:679.5']
score:985.697, rho:371.7, lambda:650.0, empty:0, scores:['area:627.0', 'major_axis_length:0.8', 'minor_axis_length:357.9']
score:260.665, rho:216.1, lambda:815.8, empty:0, scores:['area:153.3', 'major_axis_lengt

In [ ]:
s4 = shapes.subject_params['52-001']
implant, model = shapes.model_from_params(s4, biphasic=False)
model.xystep=0.25

estimator = shapes.AxonMapEstimator(implant=implant, model=model, mse_params=['area', "major_axis_length", "minor_axis_length"], loss_fn='r2', scale_features=False, resize=True)
search_params = {
    'rho': (10, 1000),
    'axlambda': (10, 2000)
}
opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=100, has_loss_function=True)

data = shapes.load_shapes("/home/yuchen/shapes/data/shapes.h5", subjects=['52-001'], stim_class='SingleElectrode')
x = data[['amp1', 'freq', 'pdur', 'electrode1']]
y = data['image']

y_moments = estimator.compute_moments(y)
averaged_moments = data
averaged_moments[['area', 'eccentricity', 'orientation']] = y_moments
averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation'].mean()
x = averaged_moments.index.to_frame().reset_index(drop=True)

train_mse = []
test_mse = []
train_size = []
test_size = []
estimator_params = []
filename_lst = []
electrode_lst=[]  # in case the server disconnects when program is running

for electrode in x.electrode1.unique():
    if electrode not in electrode_lst:
        estimator = shapes.AxonMapEstimator(implant=implant, model=model, mse_params=['area', "major_axis_length", "minor_axis_length"], loss_fn='r2', scale_features=False, resize=True)
        y_moments = estimator.compute_moments(y)
        averaged_moments = data
        averaged_moments[['area', 'eccentricity', 'orientation']] = y_moments
        averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation'].mean()
        # generate filename
        filename = 'Axon_' + 's4_' + electrode + '.pickle'
        filename_lst.append(filename)

        # get train_x and train_y
        train_x = x[x.electrode1 != electrode].reset_index(drop=True)
        train_y = averaged_moments.drop(electrode,level=2, axis=0)
        train_size.append(len(train_x))
        
        # fitting and finding the best parameter
        best_mse = 0
        best_score = 99999
        best_estimator = estimator
        for itr in range(3):
            print("Now we are fitting: " + filename[:-7] + " round " + str(itr))
            opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=100, has_loss_function=True)
            opt.fit(train_x, train_y)
            score = estimator.score(train_x, train_y,return_mses=True)
            if score[0]<best_score: 
                best_score = score[0]
                best_estimator = estimator
                best_mse = score[1]

        # store train results and estimator
        train_mse.append([best_score,best_mse])
        estimator = best_estimator
        pickle.dump(estimator, open(filename, 'wb'))
        estimator_params.append(estimator.get_params())
        
        # test (recompute y moments)
        estimator.mse_params = ['moments_central', "area", "eccentricity", "major_axis_length", "minor_axis_length", "orientation"]
        estimator.scale_features=True
        y_moments = pd.DataFrame(estimator.compute_moments(y, fit_scaler=True))
        result = pd.concat([y_moments, data[['amp1', 'freq', 'electrode1','pdur']]], axis=1, join='inner')
        test_y = result.groupby(['amp1', 'freq', 'electrode1','pdur']).mean().loc[pd.IndexSlice[:, :,electrode], :]
        test_x = x[x.electrode1 == electrode].reset_index(drop=True)

        # store test results
        test_size.append(len(test_x))
        test_mse.append(estimator.score(test_x, test_y, return_mses=True))
        
        rho = []
        axlambda = []
        train_MSE_combined = []
        train_MSE_area = []
        train_MSE_major_axis_length = []
        train_MSE_minor_axis_length = []

        test_MSE_combined = []
        test_MSE_M00 = []
        test_MSE_M02 = []
        test_MSE_M11 = []
        test_MSE_M12 = []
        test_MSE_M20 = []
        test_MSE_M21 = []
        test_MSE_M22 = []

        test_MSE_area = []
        test_MSE_eccentricity = []
        test_MSE_major_axis_length = []
        test_MSE_minor_axis_length = []
        test_MSE_orientation = []


        rho.append(estimator_params[-1]['rho'])
        axlambda.append(estimator_params[-1]['axlambda'])
        train_MSE_combined.append(train_mse[-1][0])
        train_MSE_area.append(train_mse[-1][1][0])
        train_MSE_major_axis_length.append(train_mse[-1][1][1])
        train_MSE_minor_axis_length.append(train_mse[-1][1][2])
        
        test_MSE_combined.append(test_mse[-1][0])
        test_MSE_M00.append(test_mse[-1][1][0])
        test_MSE_M02.append(test_mse[-1][1][1])
        test_MSE_M11.append(test_mse[-1][1][2])
        test_MSE_M12.append(test_mse[-1][1][3])
        test_MSE_M20.append(test_mse[-1][1][4])
        test_MSE_M21.append(test_mse[-1][1][5])
        test_MSE_M22.append(test_mse[-1][1][6])

        test_MSE_area.append(test_mse[-1][1][7])
        test_MSE_eccentricity.append(test_mse[-1][1][8])    
        test_MSE_major_axis_length.append(test_mse[-1][1][9])
        test_MSE_minor_axis_length.append(test_mse[-1][1][10])
        test_MSE_orientation.append(test_mse[-1][1][11])

        df = pd.DataFrame({'electrode':[electrode],
                       'rho':rho,
                       'axlambda':axlambda,
                       'train_combined':train_MSE_combined,
                       'train_area':train_MSE_area,
                       'train_MSE_major_axis_length':train_MSE_major_axis_length,
                       'train_MSE_minor_axis_length':train_MSE_minor_axis_length,

                       'test_combined':test_MSE_combined,
                       'test_M00':test_MSE_M00,
                       'test_M02':test_MSE_M02,
                       'test_M11':test_MSE_M11,
                       'test_M12':test_MSE_M12,
                       'test_M20':test_MSE_M20,
                       'test_M21':test_MSE_M21,
                       'test_M22':test_MSE_M22,
                       'test_area':test_MSE_area,
                       'test_eccentricity':test_MSE_eccentricity,
                       'test_major_axis_length':test_MSE_major_axis_length,
                       'test_minor_axis_length':test_MSE_minor_axis_length,
                       'test_orientation':test_MSE_orientation,


                        'train_size': [train_size[-1]],
                      'test_size':[test_size[-1]],
                      'filename':filename})
        df.to_csv("/home/yuchen/shapes/(new)estimator/" + filename[:-7] + '.csv', encoding='utf-8')